In [ ]:
!pip install spacy
!pip install nltk
!pip install contractions
#have to install the 'en_core_web_sm' model below like this because something about Jupyter Notebook
!pip install https://github.com/explosion/spacy-models/releases/download/en_core_web_sm-2.2.0/en_core_web_sm-2.2.0.tar.gz

In [ ]:
pwd

In [1]:
import spacy
import pandas as pd
import numpy as np
import nltk
from nltk.tokenize.toktok import ToktokTokenizer
import re
from bs4 import BeautifulSoup
from contractions import CONTRACTION_MAP
import unicodedata
import en_core_web_sm
import os

In [11]:
nlp = en_core_web_sm.load()
#nlp = spacy.load('en_core', parse = True, tag=True, entity=True) (DJ'S code)
#nlp_vec = spacy.load('en_vecs', parse = True, tag=True, entity=True) (DJ's code)
tokenizer = ToktokTokenizer()
##needed to use the comment out line below to get the stopwords
#nltk.download('stopwords') 
stopword_list = nltk.corpus.stopwords.words('english')
stopword_list.remove('no')
stopword_list.remove('not')

In [12]:
#function to remove accented characters
def remove_accented_chars(text):
    text = unicodedata.normalize('NFKD', text).encode('ascii', 'ignore').decode('utf-8', 'ignore')
    return text
#test the function with example
remove_accented_chars('Sómě Áccěntěd těxt')

'Some Accented text'

In [13]:
#function to expand contractions

def expand_contractions(text, contraction_mapping=CONTRACTION_MAP):
    
    contractions_pattern = re.compile('({})'.format('|'.join(contraction_mapping.keys())), 
                                      flags=re.IGNORECASE|re.DOTALL)
    def expand_match(contraction):
        match = contraction.group(0)
        first_char = match[0]
        expanded_contraction = contraction_mapping.get(match)\
                                if contraction_mapping.get(match)\
                                else contraction_mapping.get(match.lower())                       
        expanded_contraction = first_char+expanded_contraction[1:]
        return expanded_contraction
        
    expanded_text = contractions_pattern.sub(expand_match, text)
    expanded_text = re.sub("'", "", expanded_text)
    return expanded_text
#example
expand_contractions("Y'all can't expand contractions I'd think")

'You all cannot expand contractions I would think'

In [14]:
#function to remove special characters

def remove_special_characters(text, remove_digits=False):
    pattern = r'[^a-zA-z0-9\s]' if not remove_digits else r'[^a-zA-z\s]'
    text = re.sub(pattern, ' ', text)
    return text
#example
remove_special_characters("Well this was fun! What do you-think? 123#@!", 
                          remove_digits=True)

'Well this was fun  What do you think        '

In [15]:
#function to find stem words
def simple_stemmer(text):
    ps = nltk.porter.PorterStemmer()
    text = ' '.join([ps.stem(word) for word in text.split()])
    return text
#example
simple_stemmer("My system keeps crashing his crashed yesterday, ours crashes daily")

'My system keep crash hi crash yesterday, our crash daili'

In [16]:
#function for lemmatization
def lemmatize_text(text):
    text = nlp(text)
    text = ' '.join([word.lemma_ if word.lemma_ != '-PRON-' else word.text for word in text])
    return text
#example
lemmatize_text("My system keeps crashing! his crashed yesterday, ours crashes daily")

'My system keep crash ! his crash yesterday , ours crash daily'

In [17]:
#function to remove stopwords
def remove_stopwords(text, is_lower_case=False):
    tokens = tokenizer.tokenize(text)
    tokens = [token.strip() for token in tokens]
    if is_lower_case:
        filtered_tokens = [token for token in tokens if token not in stopword_list]
    else:
        filtered_tokens = [token for token in tokens if token.lower() not in stopword_list]
    filtered_text = ' '.join(filtered_tokens)    
    return filtered_text
#example
remove_stopwords("The, and, if are stopwords, computer is not")

', , stopwords , computer not'

In [18]:
#Bringing it all together — Building a Text Normalizer (comment out html stripping; not needed)
def normalize_corpus(corpus, html_stripping=True, contraction_expansion=True,
                     accented_char_removal=True, text_lower_case=True, 
                     text_lemmatization=True, special_char_removal=True, 
                     stopword_removal=True, remove_digits=True):
    
    normalized_corpus = []
    # normalize each document in the corpus
    for doc in corpus:
        # strip HTML
        #if html_stripping:
        #    doc = strip_html_tags(doc)
        # remove accented characters
        if accented_char_removal:
            print(doc)
            doc = remove_accented_chars(doc)
        # expand contractions    
        if contraction_expansion:
            doc = expand_contractions(doc)
        # lowercase the text    
        if text_lower_case:
            doc = doc.lower()
        # remove extra newlines
        doc = re.sub(r'[\r|\n|\r\n]+', ' ',doc)
        # lemmatize text
        #if text_lemmatization:
        #    doc = lemmatize_text(doc)
        # remove special characters and\or digits    
        if special_char_removal:
            # insert spaces between special characters to isolate them    
            special_char_pattern = re.compile(r'([{.(-)!}])')
            doc = special_char_pattern.sub(" \\1 ", doc)
            doc = remove_special_characters(doc, remove_digits=remove_digits)  
        # remove extra whitespace
        doc = re.sub(' +', ' ', doc)
        # remove stopwords
        if stopword_removal:
            doc = remove_stopwords(doc, is_lower_case=text_lower_case)
            
        normalized_corpus.append(doc)
        
    return normalized_corpus

In [3]:
os.chdir('C:/Users/adamj/Documents/Github/Springboard/NLP Projects/CSV Files')

In [4]:
pwd

'C:\\Users\\adamj\\Documents\\Github\\Springboard\\NLP Projects\\CSV Files'

In [5]:
os.listdir()

['augmented.csv', 'Goodreads_preprocessed.csv']

In [6]:
goodreads=open('augmented.csv','r',encoding='utf8')
goodreads_csv=pd.read_csv(goodreads)

In [7]:
pd.set_option('display.max_columns', None)
print(goodreads_csv.info())
print(goodreads_csv.head(10))

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 30005 entries, 0 to 30004
Data columns (total 19 columns):
Unnamed: 0          30005 non-null int64
title               30005 non-null object
author              30005 non-null object
author_url          30005 non-null object
rating              30005 non-null float64
voters_count        30005 non-null int64
url                 30005 non-null object
into_movie          30005 non-null int64
gender              24245 non-null object
hometown            15363 non-null object
books-num           29994 non-null float64
born-at             8183 non-null object
works-count         29994 non-null float64
publication-date    23510 non-null object
num-pages           24999 non-null float64
popular-shelves     29427 non-null object
rating-dist         29994 non-null object
publisher           24376 non-null object
book-description    28258 non-null object
dtypes: float64(4), int64(3), object(12)
memory usage: 4.3+ MB
None
   Unnamed: 0            

In [8]:
#lets inspect the numeric columns to make sure the values make sense
print(goodreads_csv.min())
print(goodreads_csv.max())
#everything seems to be fine

Unnamed: 0                                                      0
title                   "Repent, Harlequin!" Said the Ticktockman
author                                        5 Seconds of Summer
author_url      https://www.25eads.com/author/show/5601.Tom_Mc...
rating                                                          0
voters_count                                                    0
url             https://goodreads.com/book/show/1.Harry_Potter...
into_movie                                                      0
books-num                                                       1
works-count                                                     0
num-pages                                                       0
dtype: object
Unnamed: 0                                                  30004
title                   하백의 신부 [Bride of the Water God], Volume 9
author                                                 يوسف زيدان
author_url      https://www.goodreads.com/author/show/99961.Re

In [9]:
#After inspection, I'd like to split the "rating distribution column" into 6 columns.
#A column each for the 1 star votes, 2 star votes, all the way to 5 star votes.
#Also keep a column for the total votes.

#split the | in "rating distribution" column
new = goodreads_csv["rating-dist"].str.split("|", expand = True)
print(new.head())

#split the : in the columns
new0 = new[0].str.split(":", expand = True)
print(new0.head())

#split the : in the columns
new1 = new[1].str.split(":", expand = True)
print(new1.head())

#split the : in the columns
new2 = new[2].str.split(":", expand = True)
print(new2.head())

#split the : in the columns
new3 = new[3].str.split(":", expand = True)
print(new3.head())

#split the : in the columns
new4 = new[4].str.split(":", expand = True)
print(new4.head())

#split the : in the columns
new5 = new[5].str.split(":", expand = True)
print(new5.head())

# making separate 5 star column from new data frame 
goodreads_csv["5 star votes"]= new0[1] 
  
# making separate 4 star column from new data frame 
goodreads_csv["4 star votes"]= new1[1] 

# making separate 3 star column from new data frame 
goodreads_csv["3 star votes"]= new2[1] 

# making separate 2 star column from new data frame 
goodreads_csv["2 star votes"]= new3[1] 

# making separate 1 star column from new data frame 
goodreads_csv["1 star votes"]= new4[1] 

# making separate total column from new data frame 
goodreads_csv["Total Votes"]= new5[1] 

#see if new columns have been added to dataframe
print(goodreads_csv.info())

#check if values match up
print(goodreads_csv.head())

         0        1        2       3       4            5
0     5:19     4:13      3:9     2:7     1:2     total:50
1   5:5367   4:5621   3:2954   2:587   1:150  total:14679
2  5:26825  4:24784  3:17639  2:5881  1:2655  total:77784
3      5:1      4:3      3:1     2:0     1:0      total:5
4   5:3307   4:4786   3:2239   2:494   1:148  total:10974
   0      1
0  5     19
1  5   5367
2  5  26825
3  5      1
4  5   3307
   0      1
0  4     13
1  4   5621
2  4  24784
3  4      3
4  4   4786
   0      1
0  3      9
1  3   2954
2  3  17639
3  3      1
4  3   2239
   0     1
0  2     7
1  2   587
2  2  5881
3  2     0
4  2   494
   0     1
0  1     2
1  1   150
2  1  2655
3  1     0
4  1   148
       0      1
0  total     50
1  total  14679
2  total  77784
3  total      5
4  total  10974
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 30005 entries, 0 to 30004
Data columns (total 25 columns):
Unnamed: 0          30005 non-null int64
title               30005 non-null object
author          

In [10]:
#After inspection, the "title" column appears to be composed of the book title and
#the book series name. Let's split those into three columns, too.
#split the '('' in "title" column
new = goodreads_csv["title"].str.split("(", n=1, expand = True)
print(new.head(30))

#split the '#' in the other column
new2=new[1].str.split("#",n=1,expand=True)
print(new2.head(30))

#strip off the end parantheses
new3=new2[1].str.rstrip(')')
print(new3.head(30))

#strip off last character (probably a comma and space)
new4=new2[0].str[:-2]
print(new4.head(30))

#put everything together
goodreads_csv['title_clean']=new[0]
goodreads_csv['book-series']=new4
goodreads_csv['book-num-in-series']=new3

                                                    0  \
0                          The Sword and The Prophet    
1                                              Ruins    
2                                            Breathe    
3                                 The Knife-Edge Path   
4                                     The Lock Artist   
5                                         Captivated    
6                                        Turn of Mind   
7                                Let the Right One In   
8                                 The Devouring Gray    
9                               The Fill-In Boyfriend   
10                                         Hard Kill    
11                                  Rooted in Danger    
12                                       Pandaemonium   
13                               Long Walk to Freedom   
14                                   The Last Battle    
15                                The Golden Dynasty    
16                             

In [19]:
#the NLP pre-processing function won't work if there are missing values present. 
#Drop the rows that have missings in the "book description" and "popular shelves" columns
goodreads_csv_noNA = goodreads_csv.dropna(axis=0, subset=['book-description','popular-shelves'])
goodreads_csv_noNA.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 27846 entries, 0 to 30004
Data columns (total 28 columns):
Unnamed: 0            27846 non-null int64
title                 27846 non-null object
author                27846 non-null object
author_url            27846 non-null object
rating                27846 non-null float64
voters_count          27846 non-null int64
url                   27846 non-null object
into_movie            27846 non-null int64
gender                23049 non-null object
hometown              14698 non-null object
books-num             27846 non-null float64
born-at               7821 non-null object
works-count           27846 non-null float64
publication-date      22745 non-null object
num-pages             24149 non-null float64
popular-shelves       27846 non-null object
rating-dist           27846 non-null object
publisher             23499 non-null object
book-description      27846 non-null object
5 star votes          27846 non-null object
4 star vote

In [20]:
#fix some of the columns so that tehy are of the type that we want

#convert the 'votes' columns from object to integer
goodreads_csv_noNA['5 star votes']=goodreads_csv_noNA['5 star votes'].astype(str).astype(int)
goodreads_csv_noNA['4 star votes']=goodreads_csv_noNA['4 star votes'].astype(str).astype(int)
goodreads_csv_noNA['3 star votes']=goodreads_csv_noNA['3 star votes'].astype(str).astype(int)
goodreads_csv_noNA['2 star votes']=goodreads_csv_noNA['2 star votes'].astype(str).astype(int)
goodreads_csv_noNA['1 star votes']=goodreads_csv_noNA['1 star votes'].astype(str).astype(int)
goodreads_csv_noNA['Total Votes']=goodreads_csv_noNA['Total Votes'].astype(str).astype(int)

C:\Users\adamj\Anaconda3\lib\site-packages\ipykernel_launcher.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  after removing the cwd from sys.path.
C:\Users\adamj\Anaconda3\lib\site-packages\ipykernel_launcher.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """
C:\Users\adamj\Anaconda3\lib\site-packages\ipykernel_launcher.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the docu

In [21]:
#convert the date columns (which are currently strings) to date format
goodreads_csv_noNA['publication-date']= pd.to_datetime(goodreads_csv_noNA['publication-date'],
                                                      format='%m/%d/%Y',errors="coerce") 
goodreads_csv_noNA['born-at']= pd.to_datetime(goodreads_csv_noNA['born-at'],
                                                      format='%Y/%m/%d',errors="coerce") 

C:\Users\adamj\Anaconda3\lib\site-packages\ipykernel_launcher.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  This is separate from the ipykernel package so we can avoid doing imports until
C:\Users\adamj\Anaconda3\lib\site-packages\ipykernel_launcher.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """


In [22]:
goodreads_csv_noNA.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 27846 entries, 0 to 30004
Data columns (total 28 columns):
Unnamed: 0            27846 non-null int64
title                 27846 non-null object
author                27846 non-null object
author_url            27846 non-null object
rating                27846 non-null float64
voters_count          27846 non-null int64
url                   27846 non-null object
into_movie            27846 non-null int64
gender                23049 non-null object
hometown              14698 non-null object
books-num             27846 non-null float64
born-at               7786 non-null datetime64[ns]
works-count           27846 non-null float64
publication-date      22732 non-null datetime64[ns]
num-pages             24149 non-null float64
popular-shelves       27846 non-null object
rating-dist           27846 non-null object
publisher             23499 non-null object
book-description      27846 non-null object
5 star votes          27846 non-null in

In [23]:
#make columns showing percentage of votes
goodreads_csv_noNA['% 5 star votes']=goodreads_csv_noNA['5 star votes']/goodreads_csv_noNA['Total Votes']
goodreads_csv_noNA['% 4 star votes']=goodreads_csv_noNA['4 star votes']/goodreads_csv_noNA['Total Votes']
goodreads_csv_noNA['% 3 star votes']=goodreads_csv_noNA['3 star votes']/goodreads_csv_noNA['Total Votes']
goodreads_csv_noNA['% 2 star votes']=goodreads_csv_noNA['2 star votes']/goodreads_csv_noNA['Total Votes']
goodreads_csv_noNA['% 1 star votes']=goodreads_csv_noNA['1 star votes']/goodreads_csv_noNA['Total Votes']

C:\Users\adamj\Anaconda3\lib\site-packages\ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  
C:\Users\adamj\Anaconda3\lib\site-packages\ipykernel_launcher.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  This is separate from the ipykernel package so we can avoid doing imports until
C:\Users\adamj\Anaconda3\lib\site-packages\ipykernel_launcher.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = val

In [24]:
goodreads_csv_noNA.info()
goodreads_csv_noNA.head(30)

<class 'pandas.core.frame.DataFrame'>
Int64Index: 27846 entries, 0 to 30004
Data columns (total 33 columns):
Unnamed: 0            27846 non-null int64
title                 27846 non-null object
author                27846 non-null object
author_url            27846 non-null object
rating                27846 non-null float64
voters_count          27846 non-null int64
url                   27846 non-null object
into_movie            27846 non-null int64
gender                23049 non-null object
hometown              14698 non-null object
books-num             27846 non-null float64
born-at               7786 non-null datetime64[ns]
works-count           27846 non-null float64
publication-date      22732 non-null datetime64[ns]
num-pages             24149 non-null float64
popular-shelves       27846 non-null object
rating-dist           27846 non-null object
publisher             23499 non-null object
book-description      27846 non-null object
5 star votes          27846 non-null in

Unnamed: 0                                              title  \
0            0              The Sword and The Prophet (Syren, #1)   
1            1                      Ruins (Partials Sequence, #3)   
2            2                           Breathe (Sea Breeze, #1)   
4            4                                    The Lock Artist   
5            5             Captivated (The Affliction Series, #1)   
6            6                                       Turn of Mind   
7            7                               Let the Right One In   
8            8        The Devouring Gray (The Devouring Gray, #1)   
9            9                              The Fill-In Boyfriend   
10          10          Hard Kill (The Rizwan Sabir Mysteries #1)   
11          11            Rooted in Danger (Blackthorne, Inc. #3)   
12          12                                       Pandaemonium   
13          13                               Long Walk to Freedom   
14          14         The Last Battle (Chronicles of Narnia, #7)   
15          15               The Golden Dynasty (Fantasyland, #2)   
16          16                 Knife Edge (Noughts & Crosses, #2)   
17          17     The House of Hades (The Heroes of Olympus, #4)   
18          18  The Sword of Summer (Magnus Chase and the Gods...   
19          19  The Thunderbird Conspiracy: Oswald's Friend Ro...   
20          20                                   Feather And Bone   
21          21                                   The Painted Bird   
22          22                        Stunned (The Lucidites, #2)   
23          23             The Ring of Solomon (Bartimaeus, #0.5)   
24          24          B.P.R.D. Hell on Earth, Vol. 1: New World   
25          25                            Chosen (The Chosen, #1)   
26          26                                      Illuminations   
27          27                                Decay: Civilization   
28          28                                 The UnTied Kingdom   
29          29            Jupiter Rising - The Columbus Protocols   
30          30                                Flames to the Beast   

                   author                                         author_url  \
0             Missy LaRae  https://www.goodreads.com/author/show/5805389....   
1               Dan Wells  https://www.goodreads.com/author/show/2740668....   
2             Abbi Glines  https://www.goodreads.com/author/show/4872191....   
4          Steve Hamilton  https://www.goodreads.com/author/show/9891.Ste...   
5               E.M. Jade  https://www.goodreads.com/author/show/4784370....   
6          Alice LaPlante  https://www.goodreads.com/author/show/774591.A...   
7   John Ajvide Lindqvist  https://www.goodreads.com/author/show/479779.J...   
8   Christine Lynn Herman  https://www.goodreads.com/author/show/17298543...   
9              Kasie West  https://www.goodreads.com/author/show/5027236....   
10        Charlie Flowers  https://www.goodreads.com/author/show/6446070....   
11            Terry Odell  https://www.goodreads.com/author/show/897369.T...   
12  Christopher Brookmyre  https://www.goodreads.com/author/show/167572.C...   
13         Nelson Mandela  https://www.goodreads.com/author/show/367338.N...   
14             C.S. Lewis  https://www.goodreads.com/author/show/1069006....   
15         Kristen Ashley  https://www.goodreads.com/author/show/2958084....   
16       Malorie Blackman  https://www.goodreads.com/author/show/172977.M...   
17           Rick Riordan  https://www.goodreads.com/author/show/15872.Ri...   
18           Rick Riordan  https://www.goodreads.com/author/show/15872.Ri...   
19             R.K. Price  https://www.goodreads.com/author/show/3125529....   
20       Lazlo Strangolov  https://www.goodreads.com/author/show/2965285....   
21         Jerzy Kosiński  https://www.goodreads.com/author/show/11121.Je...   
22           Sarah Noffke  https://www.goodreads.com/author/show/9830676....   
23        Jonathan Strou

In [ ]:
# pre-process text and store the same
goodreads_csv_noNA['title_pre-p']=normalize_corpus(goodreads_csv_noNA['title_clean'])
goodreads_csv_noNA['book-desc_pre-p'] = normalize_corpus(goodreads_csv_noNA['book-description'])
goodreads_csv_noNA['pop-shelves_pre-p']=normalize_corpus(goodreads_csv_noNA['popular-shelves'])
goodreads_csv_noNA['author_pre-p']=normalize_corpus(goodreads_csv_noNA['author'])
#norm_corpus = list(goodreads_csv['title_clean','clean_description','popular-shelves_clean'])

The Sword and The Prophet 
Ruins 
Breathe 
The Lock Artist
Captivated 
Turn of Mind
Let the Right One In
The Devouring Gray 
The Fill-In Boyfriend
Hard Kill 
Rooted in Danger 
Pandaemonium
Long Walk to Freedom
The Last Battle 
The Golden Dynasty 
Knife Edge 
The House of Hades 
The Sword of Summer 
The Thunderbird Conspiracy: Oswald's Friend Robert Kaye
Feather And Bone
The Painted Bird
Stunned 
The Ring of Solomon 
B.P.R.D. Hell on Earth, Vol. 1: New World
Chosen 
Illuminations
Decay: Civilization
The UnTied Kingdom
Jupiter Rising - The Columbus Protocols
Flames to the Beast
Secondborn 
Garden of Lies 
Cursed 
A Special Providence
The Siren Song 
The Hot Zone: The Terrifying True Story of the Origins of the Ebola Virus
Outlander 
The Written 
The Scavenger's Daughters 
One Night with the Prince
Deadly Sanctuary 
Nightlife 
The Italian Party
Gathering 
The Big Bad Wolf Romance Compilation 
A Curious Beginning 
Star Wars: Darth Plagueis
Many Waters 
A Rose for Lancaster
The Man She Love

Daughter of Darkness
Horrorstör
Coming Home for Christmas
Bound by Ivy Forever 
Bonded in Blood 
The Last Days of Lorien 
No Easy Hope 
A Templar's Apprentice 
The Fountains of Paradise
Attack of the Fiend 
Динка 
Rise of the Poison Moon 
Those Who Watch
Desert Bound 
The Wild Rose 
The Benson 
The Maze of Bones  
Bang 
Rising Stars, Vol. 1: Born in Fire
The Piano Man
The Blood Maker and the Witch's Curse
The Robots of Dawn 
The Gilded Wolves 
The Stones of Resurrection 
The Secret Life of CeeCee Wilkes
Caitlin Star and the Guardian of Forever 
Grand Guignol Orchestra, Vol. 1
Time Jumpers 
The Shadow Rising 
Winter's Shadow 
Forsaken 
Stay with Me 
Double Time 
Wizard's Holiday 
Kitty Genovese: A True Account of a Public Murder and Its Private Consequences
Fantasy Lover 
The Queen 
The Charmer 
New England White
Unspoken 
confessions of a karaoke queen
A Little Miss Nobody; or, With the Girls of Pinewood Hall
Spartan Frost 
The Salsa Connection
Twenty Years After 
Rules of Attraction 


The Lake of Dead Languages
Shooter
Manhattan Beach
Montana Mustangs
Chasing Magic 
The Seventh Simian
Purity in Death 
The Lady and the Unicorn
My Heart Remembers
Fantasy of Freedom 
Man by a tree
Smaragdgrün 
Dark Wild Night 
Undisputed 
Doctor Who: Winner Takes All
Dirty Little Secret
Dawn of Darkness 
Future Remains
Oomph: A Little Super Goes a Long Way
The Time Fetch
Warrior's Seal 
Bagthorpes V. the World: Being the Fourth Part of the Bagthorpe Saga
31 Bond Street
Incident at Hawk's Hill
Owl's Fair 
Torn
Put The Sepia On
Betrayal 
Noble Intentions 
Highlander Heat Boxed Set
The Magic Finger
Runner 
After Dark, My Sweet
Break of Dawn 
Orbs of Trenihgea
Robopocalypse 
Restraint 
Talwar
Earth Afire 
Emma and the Vampires
Murder Red Ink
The Child Eater
Mardi Gras Zombies
As Sure as the Dawn 
Mattimeo 
Die Verschworenen 
Exiled 
The Ghosting of Gods
Empire of Storms 
The Crescent: Victory Over Adversity
The Indwelling 
Karma Girl 
Fire Dancer 
The Princess Curse
Supernova 
The Marcelli

The Warlord Wants Forever 
The Vicious Deep 
Between Shades of Gray
Nor Gold 
The Little Dragons
Cracked 
Riven 
Second Star To The Right
Nobody´s Children
Midnight Crossroad 
Engraved
Property Of
The Valley of Horses 
Pieces of a Rainbow
The Perseid Collapse 
Odd Thomas 
Bringing Adam Home: The Abduction That Changed America
Faith and Moonlight 
Green Eyed Monster
Zoe & Zak and the Ghost Leopard 
Distant Waves
The All Souls Trilogy Boxed Set
The Pull of Destiny
Spell Bound 
The Captain
Elixir 
The Heretic Queen
New Kids on the Rock 
Bill of Human Wrongs
The Lost Continent 
Black Alice
Pathways 
The Calling 
The Ghosts of Kerfol
Magic Strikes 
My Life as a Book 
The Immortal
Light In August
Black Hole Sun 
Sins of the Son 
Tornado Days
The Secret Price of History
Gateway To Heaven
Switched 
The Blood Tie 
Presumption of Innocence 
Nightshade 
The Secrets of Casanova
The Lady in Gold: The Extraordinary Tale of Gustav Klimt's Masterpiece, Portrait of Adele Bloch-Bauer
Rome 
The End Games

Let's Get Textual
Where It Began
Where Hope Begins
Nearest Thing to Crazy
Soulfarm
After Forever Ends
Healer's Touch 
The Witness
Dragon of the Stars
Fortnight Before Dawn
Chained by Night 
Where The Sun Don't Shine
The Nightmare Project: Book 1 of the Dangerous Minds Trilogy
Unexpectedly Out of Focus 
My Wolf King 
You Are Mine 
The Boat House
The Wet Woman
The Great Gilly Hopkins
Because Of You
Behind Her Eyes
Theodore Boone: Kid Lawyer 
Twice Upon a Marigold 
Cards of Love: Knight of Swords
Working for the Devil 
Live by Night 
Stolen: A Letter to My Captor
Insignia 
The Best Christmas Pageant Ever 
The Take
The Little Sisters of Eluria 
Blind Sight 
The Shifting Sands 
The Dark Continent 
The Tulip Touch
The Prague Cemetery
Street Magic 
Here Today, Gone Tomorrow 
Maid for Love 
Bitten & Smitten 
The Hypnotist 
The Mitchells: Five for Victory
Ghosts
Twelve 
Task Lyst
The Dare Ring
Identidad suspendida
Shatter Me 
Burning Bright 
Demon Road 
The Man From Berlin 
Law Man 
Graveyard o

...

<i>Drood</i>… is the name and nightmare that obsesses Charles Dickens for the last five years of his life.<br /><br />On June 9, 1865, Dickens and his mistress are secretly returning to London, when their express train hurtles over a gap in a trestle. All of the first-class carriages except the one carrying Dickens are smashed to bits in the valley below. When Dickens descends into that valley to confront the dead and dying, his life will be changed forever. And at the core of that ensuing five-year nightmare is…<br /><br /><i>Drood</i>… the name that Dickens whispers to his friend Wilkie Collins. A laudanum addict and lesser novelist, Collins flouts Victorian sensibilities by living with one mistress while having a child with another, but he may be the only man on Earth with whom Dickens can share the secret of…<br /><br /><i>Drood</i>. Increasingly obsessed with crypts, cemeteries, and the precise length of time it would take for a corpse to dissolve in a lime pit, Dickens ceases wri

Product Description<br />When Roxi Drax realises her marketing job is far from the life she imagined for herself she decides to make some serious changes. Despite her dismal financial predicament and her mother s domineering influence, Roxi searches for a life of success and contentment. With a career looming in hypnotherapy, all her resolve and enthusiasm are put to the test. But first she needs to overcome her controlling mother, her love life and more significantly her own strength of will to succeed. Sam Manty delivers a compelling tale in the novel Finger Dancing , with engrossing words to enchant the mind. The author s witty literary prose will engage the reader until the final page. <br /><br /><br />About the Author<br />Sam Manty lives in Cape Town with her husband and daughter. She s an established poet with published work in several poetry anthologies, journals and poetry websites. Her blogsite, not another blogging poet can be viewed at <a target="_blank" href="http://samma

<b>The conclusion to the thrilling memoirs of Lady Isabella Trent and her legacy of dragon evolutionary research and anthropological adventures.</b><br /><br />After nearly five decades (and, indeed, the same number of volumes), one might think they were well-acquainted with the Lady Isabella Trent--dragon naturalist, scandalous explorer, and perhaps as infamous for her company and feats of daring as she is famous for her discoveries and additions to the scientific field.<br /><br />And yet--after her initial adventure in the mountains of Vystrana, and her exploits in the depths of war-torn Eriga, to the high seas aboard The Basilisk, and then to the inhospitable deserts of Akhia--the Lady Trent has captivated hearts along with fierce minds. This concluding volume will finally reveal the truths behind her most notorious adventure--scaling the tallest peak in the world, buried behind the territory of Scirland's enemies--and what she discovered there, within the Sanctuary of Wings.
<i>Li

Maria Ridge was born a special child having gifts that allowed her to see and speak into the spirit world. As Maria aged she found these gifts to be more of a curse than a blessing. At the age of 17 Maria escaped the taunting of her family and set out on a journey that led her to discover others like herself. Ultimately this journey forces Maria to confront her past and the evil attached to her. With the help of her new friend, Allie, Maria feels she has finally found her place in this world. The destined meeting of Ash awakens the two girls to the fine line between this world and the next. Can Maria survive the haunting evil that threatens her very existence? Is she strong enough to face the past that lurks in the shadows? Will Maria embrace the truth or run from it? <br /><br />This book is based on true paranormal events. <br /><br />June of 2013 this book was revised and an additional 12000 words was added. The narrative was also changed to first person. <br /><br />Available in pa

Iris Scanlon, Half-Moon Hollow’s only daytime vampire concierge, knows more about the undead than she’d like. Running all their daylight errands—from letting in the plumber to picking up some chilled O neg—gives her a look at the not-so-glamorous side of vampire life. Her rules are strict; relationships with vamps are strictly business, not friendship—and certainly not anything else. But then she finds her newest client, Cal, poisoned on his kitchen floor, and only Iris can help.<br /> <br />Cal - who would be devastatingly sexy, if Iris allowed herself to think that way - offers Iris a hefty fee for hiding him at her place until he figures out who wants him permanently dead. Even though he’s imperious, unfriendly and doesn't seem to understand the difference between "employee" and "servant," Iris agrees, and finds herself breaking more and more of her own rules to help him - particularly those concerning nudity. <br /><br />Turns out what her quiet little life needed was some intrigue

In [ ]:
# show a sample difference
goodreads_csv_noNA.iloc[1:10][['book-description', 'book-desc_pre-p']].to_dict()

In [ ]:
#delete all occurrences of the string pattern 'br'. It is leftover from the </br />
goodreads_csv_noNA['book-desc_pre-p'] = goodreads_csv_noNA['book-desc_pre-p'].str.replace('br', '')

In [37]:
goodreads_csv_noNA.iloc[1:10][['book-description', 'book-desc_pre-p']].to_dict()

{'book-description': {1: 'Kira, Samm, and Marcus fight to prevent a final war between Partials and humans in the gripping final installment in the Partials Sequence, a series that combines the thrilling action of The Hunger Games with the provocative themes of Blade Runner and The Stand.<br /><br />There is no avoiding it—the war to decide the fate of both humans and Partials is at hand. Both sides hold in their possession a weapon that could destroy the other, and Kira Walker has precious little time to prevent that from happening. She has one chance to save both species and the world with them, but it will only come at great personal cost.',
  2: "Sadie White's summer job isn't going to be on the beach life-guarding or working at rental booths like most kids her age. With her single mother's increasing pregnancy and refusal to work, Sadie has to take over her mother's job as a domestic servant for one of the wealthy summer families on a nearby island.<br /><br />When the family arriv

In [38]:
# export to csv
goodreads_csv_noNA.to_csv("Goodreads_preprocessed2.csv",index=False)